In [11]:
%pylab inline

from glob import glob
import numpy as np
import matplotlib.pyplot as plt
import os

import base.proto
from experimental.patrick.jupyter_notebooks.helpers import init_working_directory
from mapping.distributed_mapping.proto.aligner_pb2 import AlignerSearchResult
from mapping.distributed_mapping.proto.link_evaluation_pb2 import LinkAlignmentList
from mapping.distributed_mapping.proto.link_type_enum_pb2 import LINK_ALONG, LINK_ACROSS
init_working_directory()

Populating the interactive namespace from numpy and matplotlib


In [12]:
ITERATION_DIR = '/mnt/nautilus/patrick/mapping/voxcov/mapping_test/iteration_000/'

In [13]:
links = LinkAlignmentList()
base.proto.ReadProto(os.path.join(ITERATION_DIR, 'link_alignments.pb'), links)

is_lidar = lambda x: x.link_type == LINK_ALONG or x.link_type == LINK_ACROSS

links = [link for link in links.alignments if is_lidar(link)]
print('Read {:d} alignments'.format(len(links)))

Read 2929 alignments


In [29]:
def proto_to_numpy(matrixxd_proto):
    rows, cols = matrixxd_proto.rows, matrixxd_proto.cols
    mat = np.zeros((rows, cols))
    for idx in range(rows * cols):
        mat[idx % rows, int(idx / cols)] = matrixxd_proto.data[idx]
    return mat

In [30]:
covs = []
for link in links:
    covs.append(proto_to_numpy(link.Extensions[AlignerSearchResult.ext].voxcov_result.covariance))

In [44]:
count = 0
for cov, link in zip(covs, links):
    assert np.allclose(cov, cov.T)
    
    try:
        np.linalg.cholesky(cov)
    except LinAlgError:
        count += 1
        print('===========================')
        print('From: {}-{:.3f}\tTo: {}-{:.3f}'.format(link.from_pose.vehicle, link.from_pose.time_stamp/1e9, link.to_pose.vehicle, link.to_pose.time_stamp/1e9))
        print('Matrix is not PSD:')
        print(cov)
        print('Eigenvalues: ', np.linalg.eigvals(cov))
        print(cov - cov.T)
        
print('Total: {:d}'.format(count))

From: kitt_02-1566520501.257	To: kitt_02-1566521792.178
Matrix is not PSD:
[[  1.55623635e+15   2.11958199e+15   3.52091554e+15   1.21896201e+15
   -9.73320682e+14   2.98385639e+13]
 [  2.11958199e+15   2.88685444e+15   4.79546000e+15   1.66021693e+15
   -1.32565531e+15   4.06398955e+13]
 [  3.52091554e+15   4.79546000e+15   7.96591481e+15   2.75784735e+15
   -2.20209476e+15   6.75084238e+13]
 [  1.21896201e+15   1.66021693e+15   2.75784735e+15   9.54783243e+14
   -7.62378373e+14   2.33718200e+13]
 [ -9.73320682e+14  -1.32565531e+15  -2.20209476e+15  -7.62378373e+14
    6.08746318e+14  -1.86620055e+13]
 [  2.98385639e+13   4.06398955e+13   6.75084238e+13   2.33718200e+13
   -1.86620055e+13   5.72110975e+11]]
('Eigenvalues: ', array([  0.00000000e+00+0.j        ,   1.39731073e+16+0.j        ,
        -8.30244469e-01+0.j        ,   1.59098241e-01+0.j        ,
        -7.33454624e-04+0.00349013j,  -7.33454624e-04-0.00349013j]))
[[ 0.         -0.75        0.         -1.25        0.125     